In [1]:
import numpy as np
import pandas as pd
import math as m
from statsmodels.tsa.stattools import acf
from statsmodels.graphics.tsaplots import plot_acf
from scipy import *
import scipy.linalg
import torch
from torch import nn, optim
import mpl_toolkits.mplot3d.axes3d as p3
from sklearn.datasets import make_swiss_roll
from sklearn.preprocessing import MinMaxScaler


import scaleogram as scg
import matplotlib.pyplot as plt
import warnings

from visuals import *
from my_lib import *
from SSA_lib import SSA

In [2]:
warnings.simplefilter('ignore')

plt.rcParams['figure.figsize'] = 16, 8
plt.rcParams['font.family'] = 'DejaVu Serif'
plt.rcParams['lines.linewidth'] = 2
plt.rcParams['lines.markersize'] = 8
plt.rcParams['xtick.labelsize'] = 16
plt.rcParams['ytick.labelsize'] = 16
plt.rcParams['legend.fontsize'] = 16
plt.rcParams['axes.titlesize'] = 24
plt.rcParams['axes.labelsize'] = 8

In [3]:
device = ('cuda' if torch.cuda.is_available() else 'cpu')

In [4]:
dt = 459*20
#data = pd.read_csv('data/long_walk_100_acc.csv', delimiter =';', decimal=',')[3815+6*455:3815+6*455+dt]
data = pd.read_csv('data/long_walk_100_acc.csv', delimiter =';', decimal=',')[7009:7009+dt]
#data = pd.read_csv('data/long_walk_100_acc.csv', delimiter =';', decimal=',')[3785:8000]
#data = pd.read_csv('data/home_lin_10_lac.csv', delimiter =';', decimal=',')[:]
frecuency = len(data)/(data['time'].values[-1]-data['time'].values[0])
assert 480 < frecuency < 520

x_acc = ( (data['X_value'].values)**2 + (data['Y_value'].values)**2 + (data['Z_value'].values)**2)**.5
_m = np.mean(x_acc)
x_acc -= _m
t = (data['time'].values).astype(float).reshape([-1,])
t = np.linspace(0,t[-1]-t[0],len(x_acc))

fig = go.Figure()
fig.add_scatter(y = x_acc, mode='lines', name='Sum squares')
fig.show()

In [5]:
accel_ssa = SSA(x_acc, 500)

In [6]:
x_acc_clear = accel_ssa.reconstruct(slice(0,5))

In [7]:
def HankelMatrix(X, L):  
    N = X.shape[0]
    return scipy.linalg.hankel(X[ : N - L + 1], X[N - L : N])

In [8]:
track2, basis2 = phase_track(np.array([x_acc_clear]).T, 600, 3)
plot_phase_track(track2)

Explained variation for 3 principal components: [0.40011295 0.3676284  0.11352861]
Cumulative explained variationfor 3 principal components: 0.8812699616005983



In [9]:
X = HankelMatrix(x_acc_clear,600)
x = torch.from_numpy(X).to(device)

In [10]:
class Autoencoder(nn.Module):
    """Makes the main denoising auto

    Parameters
    ----------
    in_shape [int] : input shape
    enc_shape [int] : desired encoded shape
    """

    def __init__(self, in_shape, enc_shape):
        super(Autoencoder, self).__init__()
        
        self.encode = nn.Sequential(
            nn.Linear(in_shape, 512),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(512, 256),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(256, 128),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(128, 64),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(64, enc_shape),
        )
        
        self.decode = nn.Sequential(
            nn.BatchNorm1d(enc_shape),
            nn.Linear(enc_shape, 64),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(64, 128),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(128, 256),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(256, 512),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(512, in_shape)
        )
        
    def forward(self, x):
        x = self.encode(x)
        x = self.decode(x)
        return x
    
encoder = Autoencoder(in_shape=600, enc_shape=3).double().to(device)

error = nn.MSELoss()

optimizer = optim.Adam(encoder.parameters())

def train(model, error, optimizer, n_epochs, x):
    model.train()
    for epoch in range(1, n_epochs + 1):
        optimizer.zero_grad()
        output = model(x)
        loss = error(output, x)
        loss.backward()
        optimizer.step()
        
        if epoch % int(0.1*n_epochs) == 0:
            print(f'epoch {epoch} \t Loss: {loss.item():.4g}')

In [11]:
train(encoder, error, optimizer, 5000, x)

epoch 5 	 Loss: 16.76
epoch 10 	 Loss: 15.62
epoch 15 	 Loss: 12.27
epoch 20 	 Loss: 10.93
epoch 25 	 Loss: 9.86
epoch 30 	 Loss: 8.861
epoch 35 	 Loss: 7.716
epoch 40 	 Loss: 6.624
epoch 45 	 Loss: 5.56
epoch 50 	 Loss: 5.404


In [12]:
with torch.no_grad():
    encoded = encoder.encode(x)
    decoded = encoder.decode(encoded)
    mse = error(decoded, x).item()
    enc = encoded.cpu().detach().numpy()
    dec = decoded.cpu().detach().numpy()

In [13]:
enc

array([[ 19.16735861,  -3.89364322,   6.07172941],
       [ 23.33382263,   5.17828349,  10.13841426],
       [ 36.66103837,  10.9399361 ,  14.87565784],
       ...,
       [  2.12950278,  14.37480549, -20.77604333],
       [ 18.00904877,  23.03126486, -26.59172394],
       [ 11.94275031,  29.50445845, -42.17603225]])

In [14]:
fig_2 = go.Figure()


fig_2.add_trace(go.Scatter3d(x=enc[:,0][::],
                             y=enc[:,1][::],
                             z=enc[:,2][::],
                             #mode='markers',
                             marker=dict(
                                         size=0.1,
                                         line=dict(
                                                    width=0.01
                                                  )

                                         ),
                             name='trajectory'
                            )
                )


fig_2.layout.template = 'plotly_white'
fig_2.show()

In [15]:
Sphere_projection(enc, n = 1)